# Connect

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


# Install

In [ ]:
!pip install -U sentence-transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 171.5/171.5 kB 5.2 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl (176.2 MB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-m

In [ ]:
!pip install numpy requests nlpaug

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.5/410.5 kB 11.4 MB/s eta 0:00:00


In [ ]:
!pip install nltk>=3.4.5

In [ ]:
!pip install transformers

In [ ]:
!python -m spacy download ro_core_news_sm

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.9/12.9 MB 16.0 MB/s eta 0:00:00
✔ Download and installation successful
You can now load the package via spacy.load('ro_core_news_sm')
⚠ Restart to reload dependencies
If you are in a Jupyter or Colab notebook, you may need to restart Python in
order to load all the package's dependencies. You can do this by selecting the
'Restart kernel' or 'Restart runtime' option.


# Imports

In [ ]:
import re
import nltk
import datetime
import pandas as pd
from nltk.corpus import stopwords
from transformers import AutoModelForMaskedLM, AutoTokenizer
import string
import time
import numpy as np

In [ ]:
import spacy
import random

# Config

In [ ]:
class config:
  STOP_WORDS = '/content/gdrive/stopwords-ro.txt'
  WANDB_KEY = 'xxxx'
  DATASET_PATH = '/content/df_rare_augmentations.csv'
  text_test = "Magazinul ok dar deranjatnti sunt copii scapati de sub controlul parintilor , alearga cu biciclete, trotinete fara sa se uite si lovesc persoane si mai grav alti copii.Sa se faca un loc de joaca special amenajat pentru ei."
  aspects_test = "Magazinul ok; deranjatnti sunt copii scapati de sub controlul parintilor , alearga cu biciclete, trotinete fara sa se uite si lovesc persoane si mai grav alti copii; "

# Read Data

In [ ]:
df = pd.read_csv(config.DATASET_PATH)

In [ ]:
if 'Unnamed: 0.1' and 'Unnamed: 0' in df.columns:
  df.drop(columns=['Unnamed: 0.1','Unnamed: 0'], inplace=True)

In [ ]:
# df.drop(columns=['polarity_aspect','category_aspect','all_categories','aspect'], inplace=True)

In [ ]:
df.head(2)

text      id all_categories  \
0  Am comandat produsele luni si le-am primit sâm...  421321       delivery   
1  am comandat 2 ceasuri si unul a fost livrat cu...  421322       delivery   

                                             all_ate all_polarities  \
0  Am comandat produsele luni si le-am primit sâm...       Negative   
1  am comandat 2 ceasuri si unul a fost livrat cu...       Negative   

  data_origin                                       text_cleaned  \
0      manual  Am comandat produsele luni si le-am primit sâm...   
1      manual  am comandat 2 ceasuri si unul a fost livrat cu...   

  all_categories_old  
0           delivery  
1           delivery

In [ ]:
def get_aspects_list(concatenated_aspects):
  aspects_list = concatenated_aspects.split(';')
  aspects_list = [a.strip() for a in aspects_list if a!=' ']
  return aspects_list

In [ ]:
get_aspects_list(df.iloc[0]['all_ate'])

['Am comandat produsele luni si le-am primit sâmbăta...prea mult timp...']

In [ ]:
df[df['text_cleaned'].apply(type) != str]

Empty DataFrame
Columns: [text, id, all_categories, all_ate, all_polarities, data_origin, text_cleaned, all_categories_old]
Index: []

In [ ]:
df.dropna(subset=['text_cleaned'],inplace=True)
df[df['text_cleaned'].apply(type) != str]

Empty DataFrame
Columns: [text, id, all_categories, all_ate, all_polarities, data_origin, text_cleaned, all_categories_old]
Index: []

# MLM

## load pretrained models

In [ ]:
# https://medium.com/@thedatabeast/mask-language-modeling-a-comprehensive-guide-b86edf5fd214
import torch
from transformers import BertTokenizer, BertForMaskedLM

model_name = 'bert-base-uncased'
tokenizer = BertTokenizer.from_pretrained(model_name)
model = BertForMaskedLM.from_pretrained(model_name)

tokenizer_config.json:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'bert.pooler.dense.weight', 'bert.pooler.dense.bias']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


### test mlm

In [ ]:
# Define input text
text = "I like doing nothin from [MASK] to time."

# Tokenize the input text
tokens = tokenizer.tokenize(text)
masked_index = tokens.index('[MASK]')

# Convert tokens to tensor
token_ids = tokenizer.convert_tokens_to_ids(tokens)
input_tensor = torch.tensor([token_ids])

# Predict the missing word
with torch.no_grad():
    outputs = model(input_tensor)
    predictions = outputs[0][0, masked_index].topk(5)

# Print the predicted words
predicted_words = [tokenizer.convert_ids_to_tokens(idx.item()) for idx in predictions.indices]
print("Predicted words:", predicted_words)

Predicted words: ['time', 'up', 'going', 'way', 'down']


## mlm using hf pipeline mlm

In [ ]:
from transformers import pipeline
import pandas as pd
import os
from random import randint
import spacy
import string

nlp_spacy = spacy.load('ro_core_news_sm')
checkpoint = 'dumitrescustefan/bert-base-romanian-cased-v1'

mask_filler = pipeline("fill-mask", checkpoint)
mask_token = mask_filler.tokenizer.mask_token

config.json:   0%|          | 0.00/385 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/500M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/29.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/397k [00:00<?, ?B/s]

In [ ]:
import string
punctuation = string.punctuation
punctuation = re.sub('-','',punctuation)
punctuation

'!"#$%&\'()*+,./:;<=>?@[\\]^_`{|}~'

In [ ]:
with open(config.STOP_WORDS) as file:
  stopwords = [line.rstrip() for line in file]
stopwords

['a',
 'abia',
 'acea',
 'aceasta',
 'această',
 'aceea',
 'aceeasi',
 'acei',
 'aceia',
 'acel',
 'acela',
 'acelasi',
 'acele',
 'acelea',
 'acest',
 'acesta',
 'aceste',
 'acestea',
 'acestei',
 'acestia',
 'acestui',
 'aceşti',
 'aceştia',
 'acolo',
 'acord',
 'acum',
 'adica',
 'ai',
 'aia',
 'aibă',
 'aici',
 'aiurea',
 'al',
 'ala',
 'alaturi',
 'ale',
 'alea',
 'alt',
 'alta',
 'altceva',
 'altcineva',
 'alte',
 'altfel',
 'alti',
 'altii',
 'altul',
 'am',
 'anume',
 'apoi',
 'ar',
 'are',
 'as',
 'asa',
 'asemenea',
 'asta',
 'astazi',
 'astea',
 'astfel',
 'astăzi',
 'asupra',
 'atare',
 'atat',
 'atata',
 'atatea',
 'atatia',
 'ati',
 'atit',
 'atita',
 'atitea',
 'atitia',
 'atunci',
 'au',
 'avea',
 'avem',
 'aveţi',
 'avut',
 'azi',
 'aş',
 'aşadar',
 'aţi',
 'b',
 'ba',
 'bine',
 'bucur',
 'bună',
 'c',
 'ca',
 'cam',
 'cand',
 'capat',
 'care',
 'careia',
 'carora',
 'caruia',
 'cat',
 'catre',
 'caut',
 'ce',
 'cea',
 'ceea',
 'cei',
 'ceilalti',
 'cel',
 'cele',
 'ce

In [ ]:
punctuation_list = [p for p in punctuation]
punctuation_list

['!',
 '"',
 '#',
 '$',
 '%',
 '&',
 "'",
 '(',
 ')',
 '*',
 '+',
 ',',
 '.',
 '/',
 ':',
 ';',
 '<',
 '=',
 '>',
 '?',
 '@',
 '[',
 '\\',
 ']',
 '^',
 '_',
 '`',
 '{',
 '|',
 '}',
 '~']

In [ ]:
stopwords.extend(punctuation_list)

In [ ]:
import random

def choose_random_index(words, blacklist_words, prev_idxs):

    found_index = len(words)
    found=False
    call_again = True
    check =  all(item in blacklist_words for item in words)
    if check:
      call_again = False
      return found_index-1, call_again
    already_tested_idxs = prev_idxs

    while found==False:
        choices = list(set(range(len(words)-1)).difference(already_tested_idxs))
        if len(choices)<1:
          call_again=False
          return 'no', call_again

        random_index = random.choice(choices)
        already_tested_idxs.append(random_index)

        for idx, word in enumerate(words):
            if idx==random_index:
              if word in blacklist_words:
                found = False
              elif word in stopwords:
                found = False
              else:
                found = True
                found_index = random_index

    return found_index, call_again

In [ ]:
sents_except = []

def get_all_dependencies(sentence, target_sequence):
    global nlp_spacy
    target_sequence = target_sequence.translate(str.maketrans(' ', ' ', string.punctuation))
    target_seq_words = target_sequence.split(' ')

    doc_source = nlp_spacy(sentence)
    doc_target = nlp_spacy(target_sequence)

    indices = {}
    for token in doc_source:
        if token.text in target_seq_words:
            indices[token.text] = token.i

    depenedent_tokens = {'target_token':[],'token_dep':[]}

    for target_token in doc_target:
        try:
          idx = indices[target_token.text]
          depenedent_tokens['target_token'].append(target_token.text)
          span_token = doc_source[idx:idx+1]  # identify token in source text
          for current_source_token in doc_source:
              if current_source_token.pos_ in ['VERB','NOUN','ADJ','PROPN']:
                  for child in current_source_token.children:
                      if span_token.text==child.text:
                          depenedent_tokens['token_dep'].append(current_source_token.text)
                          break
        except:
          print('Excep:', target_token.text)
          continue

    return depenedent_tokens

def replace_new_index(new_words, blacklist_words, top_k, prev_idxs):
  K1, call_again = choose_random_index(new_words, blacklist_words, prev_idxs)

  if K1!='no':
    masked_sentence = " ".join(new_words[:K1]  + [mask_token] + new_words[K1+1:])

    if top_k < 2:
      top_k+=1

    predictions = mask_filler(masked_sentence, top_k=top_k)

    try:
      augmented_sequences = [predictions[i]["sequence"] for i in range(top_k) if predictions[i]['token_str'].lower() not in [w.lower() for w in new_words] ]
      tokens = [predictions[i]["token_str"] for i in range(top_k) if predictions[i]['token_str'].lower() not in [w.lower() for w in new_words] ]
      if len(augmented_sequences)>1:
        return K1, augmented_sequences[1],tokens[1], call_again
      elif len(augmented_sequences) > 0:
        return K1, augmented_sequences[0],tokens[0], call_again
    except:
      print('Other exceptions:',augmented_sequences,call_again,K1 )
      return K1, [],[], call_again
  else:
    return K1, [],[], call_again


def augment_data_hfpipeline(sentence, blacklist, avoid_dependency, top_k):
  global sents_except
  """top_k must be greater than 1"""
  num_iter= int(len(sentence.split())*15/100)

  blacklist = ' '.join(get_aspects_list(blacklist))
  blacklist_words = blacklist.split(' ')
  words = sentence.split(' ')
  new_words = []

  words = [new_words.extend(word.split( )) for word in words]

  if avoid_dependency==True:
    dep_tokens = get_all_dependencies(' '.join(new_words),' '.join(blacklist_words))['token_dep']
    blacklist_words.extend(dep_tokens)

  new_sentences = []
  prev_idxs=[]
  for experiment in range(num_iter):
    try:
      idx, sent, token, call_again = replace_new_index(new_words, blacklist_words, top_k, prev_idxs)
      words = sent.split(' ')
      new_words = []
      words = [new_words.extend(word.split( )) for word in words]
      blacklist_words.append(token)
      print('replaced token:', token)
      if call_again==False:
        break
      else:
        prev_idxs.append(idx)
        new_sentences.append(sent)
    except:
      sents_except.append(sentence)
      print('Exception for iter ', experiment, '\n',f'{new_words=}',f'{blacklist_words=}',f'{top_k=}',f'{prev_idxs=}')

  if len(new_sentences)>1:
    return new_sentences[-1]
  else:
    return []

In [ ]:
df.iloc[100]['text_cleaned']

'Am facut cumparaturi de 3000 de lei ultima oara si de la casa de marcat mi s-a spus ca voi primi un voucher de 750 lei pt a-l folosi data viitoare. Asta se intampla sapt trecuta si nici pana in ziua de azi nu am primit acel voucher pe mail...'

In [ ]:
augment_data_hfpipeline(df.iloc[100]['text_cleaned'], df.iloc[100]['all_ate'], True,5)

replaced token: le
replaced token: .
replaced token: viitoare
replaced token: produse
replaced token: făcut
replaced token: 1000
replaced token: s


'Am făcut cumparaturi de 1000 de lei ultima oara si de la casa de marcat mi s a spus ca voi primi un voucher de 750 lei pt le produse data viitoare Asta se intampla sapt trecuta si nici pana in ziua de azi nu am primit acel voucher pe mail...'

In [ ]:
augment_data_hfpipeline("Sunt foarte multumita de acest magazin. il recomand ori de cate ori am ocazia", "Sunt foarte multumita; recomand " , True, 5)

replaced token: câte
replaced token: aparat


'Sunt foarte multumita de acest aparat il recomand ori de câte ori am ocazia'

In [ ]:
print('Original text:',df.iloc[1]['text_cleaned'])
print('MLM text:',augment_data_hfpipeline(df.iloc[1]['text_cleaned'], df.iloc[1]['all_ate'], True,5))

Original text: am comandat 2 ceasuri si unul a fost livrat cu tot cu antifurtul din magazin, deci termnul s-a lungit la 4 zile
Excep: sa
replaced token: luni
MLM text: []


In [ ]:
df.iloc[5]['all_ate'], df.iloc[5]['text_cleaned']

('Din păcate nu am primit comanda pana astăzi .Fiind plasata de 5 zile,ma așteptam sa ajungă ceva mai repede.',
 'Din păcate nu am primit comanda pana astăzi .Fiind plasata de 5 zile,ma așteptam sa ajungă ceva mai repede.')

In [ ]:
augment_data_hfpipeline(df.iloc[5]['text_cleaned'], df.iloc[5]['all_ate'], True,5)

Excep: Fiind
Excep: zilema
replaced token: devreme


[]

## apply mlm on all instances

In [ ]:
for idx, row in df.iterrows():
  aspects = row['all_ate']
  source_text = row['text_cleaned']
  modified_text = augment_data_hfpipeline(source_text, aspects, True, 5)
  print(f'{source_text=}')
  print(f'{modified_text=}')
  print(f'{aspects=}')
  break

Excep: leam
Excep: sâmbătaprea
replaced token: !
source_text='Am comandat produsele luni si le-am primit sâmbăta...prea mult timp...'
modified_text=[]
aspects='Am comandat produsele luni si le-am primit sâmbăta...prea mult timp...'


In [ ]:
contains_non_string = df[df['text_cleaned'].apply(type) != str]
contains_non_string

Empty DataFrame
Columns: [text, id, all_categories, all_ate, all_polarities, data_origin, text_cleaned, all_categories_old]
Index: []

In [ ]:
df['text_mlm'] = df.apply(lambda x: augment_data_hfpipeline(x['text_cleaned'],x['all_ate'],True,5), axis=1)
df

Streaming output truncated to the last 5000 lines.
replaced token: bune
Excep: Livrarea
Excep: Mias
replaced token: felicit
replaced token: Ma
replaced token: avantaj
Excep: miar
replaced token: produselor
replaced token: asta
replaced token: (
replaced token: am
replaced token: fiu
replaced token: costum
replaced token: produsele
replaced token: igiena
replaced token: altul
Excep: sa
replaced token: iar
Exception for iter  0 
 new_words=['Nu', 'sunt', 'promoții', 'si', 'la', 'produsele', '""ultimele', 'rămase""', 'calitatea', 'lasa', 'de', 'dorit...'] blacklist_words=['Nu', 'sunt', 'promoții', 'si', 'la', 'produsele', '""ultimele', 'rămase""', 'calitatea', 'lasa', 'de', 'dorit', 'rămase', 'promoții', 'produsele', 'rămase', 'calitatea', 'calitatea', 'dorit', 'lasa'] top_k=5 prev_idxs=[9, 8, 5, 2, 1, 4, 0, 10, 3, 7, 6]
Excep: Liviudaca
replaced token: nostri
replaced token: orice
replaced token: vine
replaced token: bune
Excep: medie
replaced token: In
replaced token: ##a
replaced token

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
replaced token: ,
replaced token: iar
replaced token: cliente
replaced token: +
replaced token: numai
replaced token: bun
replaced token: cazul
replaced token: vad
replaced token: asteptat
replaced token: fac
replaced token: aceea
replaced token: ars
replaced token: kit
replaced token: .
replaced token: premii
replaced token: Doar
replaced token: `
replaced token: recomanda
replaced token: acesta
replaced token: produs
replaced token: deplasa
Excep: completaProbabil
Excep: completaProbabil
replaced token: primi
Excep: disponibilisi
replaced token: …
Excep: comandaacum
Excep: skiurilorbun
replaced token: .
replaced token: ##i
replaced token: .
replaced token: caute
Excep:  
replaced token: box
Excep: ma
Excep: intro
Excep: ziuaSunt
Excep: ma
Excep: intro
Excep: m
Excep: ma
Excep: intro
replaced token: .
Excep: casaa
replaced token: ?
Excep:  
Excep: eaAdică
Excep: wtf
replaced token: ?
replaced token: !
Excep: Sa
Excep: nam
replaced tok

text      id  \
0     Am comandat produsele luni si le-am primit sâm...  421321   
1     am comandat 2 ceasuri si unul a fost livrat cu...  421322   
2     Cred ca ar trebui lucrat la o parte din angaja...  421323   
3     Prima data cand am fost in magazin nu era pe s...  421324   
4     foarte slab aprovizionat,nu am gasit produsele...  421325   
...                                                 ...     ...   
3871  Raioanele aglomerate sa detina personal sufici...  415729   
3872  Am fost la voi in magazin in data de 25.05.201...  415731   
3873  Am fost placut impresionat de disponibilitatea...  415732   
3874  Un numar mai mare de personal cred ca ar fi de...  415735   
3875  Am vrut sa ii iau la cel mic o vestuta si de f...  415736   

                                         all_categories  \
0                                              delivery   
1                                              delivery   
2                                      staff competency   
3                                        shop diversity   
4                                        shop diversity   
...                                                 ...   
3871                                 staff availability   
3872                          staff competency; service   
3873  product; quality; price; return warranty; staf...   
3874                                 staff availability   
3875                                     shop diversity   

                                                all_ate  \
0     Am comandat produsele luni si le-am primit sâm...   
1     am comandat 2 ceasuri si unul a fost livrat cu...   
2     Cred ca ar trebui lucrat la o parte din angaja...   
3     Prima data cand am fost in magazin nu era pe s...   
4     foarte slab aprovizionat,nu am gasit produsele...   
...                                                 ...   
3871  Raioanele aglomerate sa detina personal suficient   
3872  Am fost la voi in magazin in data de 25.05.201...   
3873  Rucsacul foarte bine lucrat, cu materiale de c...   
3874  Un numar mai mare de personal cred ca ar fi de...   
3875  Am vrut sa ii iau la cel mic o vestuta si de f...   

                                         all_polarities data_origin  \
0                                              Negative      manual   
1                                              Negative      manual   
2                                              Negative      manual   
3                                              Negative      manual   
4                                              Negative      manual   
...                                                 ...         ...   
3871                                           Negative      manual   
3872                                 Positive; Positive      manual   
3873  Positive; Positive; Negative; Negative; Positi...      manual   
3874                                           Negative      manual   
3875                                           Negative      manual   

                                           text_cleaned  \
0     Am comandat produsele luni si le-am primit sâm...   
1     am comandat 2 ceasuri si unul a fost livrat cu...   
2     Cred ca ar trebui lucrat la o parte din angaja...   
3     Prima data cand am fost in magazin nu era pe s...   
4     foarte slab aprovizionat,nu am gasit produsele...   
...                                                 ...   
3871  Raioanele aglomerate sa detina personal sufici...   
3872  Am fost la voi in magazin in data de 25.05.201...   
3873  Am fost placut impresionat de disponibilitatea...   
3874  Un numar mai mare de personal cred ca ar fi de...   
3875  Am vrut sa ii iau la cel mic o vestuta si de f...   

                                     all_categories_old  \
0                                              delivery   
1                                              delivery   
2                                      staff competency   
3                             

In [ ]:
mask = df['text_cleaned']==df['text_mlm']

In [ ]:
mask

0       False
1       False
2       False
3       False
4       False
        ...  
3871    False
3872    False
3873    False
3874    False
3875    False
Length: 3876, dtype: bool

In [ ]:
df = df[~mask]

In [ ]:
df.columns

Index(['text', 'id', 'all_categories', 'all_ate', 'all_polarities',
       'data_origin', 'text_cleaned', 'text_mlm'],
      dtype='object')

In [ ]:
augmented_data = df[['text_mlm','id','all_categories','all_ate','all_polarities']]
augmented_data['data_origin'] = 'mlm'


<ipython-input-40-d6409719d499>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  augmented_data['data_origin'] = 'mlm'


In [ ]:
assert augmented_data[augmented_data['id']==421323]['text_mlm'].values[0]==[]

In [ ]:
def to_keep(row):
  value = row['text_mlm']
  # print(value)
  if value==[]:
    return False
  else:
    return True

In [ ]:
augmented_data['keep']=augmented_data.apply(lambda x: to_keep(x),axis=1)

<ipython-input-42-99cf919ca4a6>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  augmented_data['keep']=augmented_data.apply(lambda x: to_keep(x),axis=1)


In [ ]:
augmented_data = augmented_data[augmented_data['keep']==True]
augmented_data

text_mlm      id  \
10    Au mers la serviciul de paza pe un scaun pe ca...  421331   
11    Mai multa communicativitate nu strica niciodat...  421332   
13    Comunicarea cu personalul magazinului este foa...  421334   
14    lipsa marimilor mari la inbracaminte 5xl, 6xl!...  421336   
16    Nu am beneficiat de vreo reducere de pe urma c...  421338   
...                                                 ...     ...   
3845  Preturile sunt bune si produsele de calitate. ...  415688   
3858  Colaborarea cu mult entuziasm din partea consu...  415707   
3863  E in magazin cu mare diversitate de oferte pre...  415717   
3868  in casa este totul in ordine Varietatea de art...  415722   
3871  Raioanele aglomerate sa detina controlul dar e...  415729   

                                  all_categories  \
10                              staff competency   
11                              staff competency   
13                    staff competency; delivery   
14                         shop diversity; price   
16                                       service   
...                                          ...   
3845  price; quality; product; shop organization   
3858                            staff competency   
3863     staff competency; shop diversity; price   
3868                              shop diversity   
3871                          staff availability   

                                                all_ate  \
10    domnul responsabil a parut a fi deranjat si m-...   
11      Mai multa communicativitate nu strica niciodata   
13    Comunicarea cu personalul magazinului este foa...   
14    lipsa marimilor mari la inbracaminte 5xl,6xl;p...   
16    Nu am beneficiat de vreo reducere de pe urma c...   
...                                                 ...   
3845  Preturile sunt bune si produsele de calitate. ...   
3858  mai mult entuziasm din partea consultantilor a...   
3863  personal amabil ,rapid si eficient;E in magazi...   
3868  Varietatea de articole pt. copii ar trebui sa ...   
3871  Raioanele aglomerate sa detina personal suficient   

                              all_polarities data_origin  keep  
10                                  Negative         mlm  True  
11                                  Negative         mlm  True  
13                        Negative; Negative         mlm  True  
14                        Negative; Negative         mlm  True  
16                                  Negative         mlm  True  
...                                      ...         ...   ...  
3845  Positive; Positive; Positive; Negative         mlm  True  
3858                                Negative         mlm  True  
3863            Positive; Positive; Positive         mlm  True  
3868                                Negative         mlm  True  
3871                                Negative         mlm  True  

[941 rows x 7 columns]

In [ ]:
augmented_data.drop(columns=['keep'], inplace=True)

<ipython-input-86-7c23c1653868>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  augmented_data.drop(columns=['keep'], inplace=True)


In [ ]:
augmented_data.rename(columns={'text_mlm':'text_cleaned'}, inplace=True)

<ipython-input-101-dcbf1698dcb3>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  augmented_data.rename(columns={'text':'text_cleaned'}, inplace=True)


In [ ]:
augmented_data.to_csv('mlm_result.csv', index=False)

In [ ]:
df_initial = df.drop(columns=['text_mlm','text'])

In [ ]:
new_df = pd.concat([augmented_data,df_initial], ignore_index=True,axis=0)

In [ ]:
new_df

text_cleaned      id  \
0     Am comandat produsele luni si le - am primit s...  421321   
1     am comandat 2 ceasuri si unul a fost livrat cu...  421322   
2     foarte slab aprovizionat, nu am gasit produsel...  421325   
3     Din păcate nu am primit comanda pana astăzi. F...  421326   
4     Magazin slab aprovizionat in special cu produs...  421327   
...                                                 ...     ...   
1912  Totul este de calitate la un preț bun de aseme...  422479   
1913  Stocul este insuficient fata de cate produse s...  422480   
1914  Angajații sunt foarte atenți cu cei care cumpa...  422481   
1915  atmosfera placuta in magazin; as recomanda mai...  422482   
1916  Foarte placut surprins ca am gasit un model de...  422483   

                         all_categories  \
0                              delivery   
1                              delivery   
2                        shop diversity   
3                              delivery   
4                        shop diversity   
...                                 ...   
1912              quality;price;service   
1913                     shop diversity   
1914                   staff competency   
1915                environment;product   
1916  tech support;shop diversity;price   

                                                all_ate  \
0     Am comandat produsele luni si le-am primit sâm...   
1     am comandat 2 ceasuri si unul a fost livrat cu...   
2     foarte slab aprovizionat,nu am gasit produsele...   
3     Din păcate nu am primit comanda pana astăzi .F...   
4     Magazin slab aprovizionat in special cu produs...   
...                                                 ...   
1912  Totul este de calitate;la un preț bun;servicii...   
1913  Stocul este insuficient fata de cate produse s...   
1914  Angajații sunt foarte atenți cu cei care cumpa...   
1915  atmosfera placuta in magazin;as recomanda mai ...   
1916  nu aparea pe site modelul;Foarte placut surpri...   

                    all_polarities data_origin  
0                         Negative         mlm  
1                         Negative         mlm  
2                         Negative         mlm  
3                         Negative         mlm  
4                         Negative         mlm  
...                            ...         ...  
1912  Positive; Positive; Positive      manual  
1913                      Negative      manual  
1914                      Positive      manual  
1915             Positive; Neutral      manual  
1916  Negative; Positive; Positive      manual  

[1917 rows x 6 columns]

In [ ]:
new_df.to_csv('mlmAndTrainData.csv', index=False)

In [ ]:
new_df

text_cleaned      id  \
0     Am comandat produsele luni si le - am primit s...  421321   
1     am comandat 2 ceasuri si unul a fost livrat cu...  421322   
2     foarte slab aprovizionat, nu am gasit produsel...  421325   
3     Din păcate nu am primit comanda pana astăzi. F...  421326   
4     Magazin slab aprovizionat in special cu produs...  421327   
...                                                 ...     ...   
1912  Totul este de calitate la un preț bun de aseme...  422479   
1913  Stocul este insuficient fata de cate produse s...  422480   
1914  Angajații sunt foarte atenți cu cei care cumpa...  422481   
1915  atmosfera placuta in magazin; as recomanda mai...  422482   
1916  Foarte placut surprins ca am gasit un model de...  422483   

                         all_categories  \
0                              delivery   
1                              delivery   
2                        shop diversity   
3                              delivery   
4                        shop diversity   
...                                 ...   
1912              quality;price;service   
1913                     shop diversity   
1914                   staff competency   
1915                environment;product   
1916  tech support;shop diversity;price   

                                                all_ate  \
0     Am comandat produsele luni si le-am primit sâm...   
1     am comandat 2 ceasuri si unul a fost livrat cu...   
2     foarte slab aprovizionat,nu am gasit produsele...   
3     Din păcate nu am primit comanda pana astăzi .F...   
4     Magazin slab aprovizionat in special cu produs...   
...                                                 ...   
1912  Totul este de calitate;la un preț bun;servicii...   
1913  Stocul este insuficient fata de cate produse s...   
1914  Angajații sunt foarte atenți cu cei care cumpa...   
1915  atmosfera placuta in magazin;as recomanda mai ...   
1916  nu aparea pe site modelul;Foarte placut surpri...   

                    all_polarities data_origin  
0                         Negative         mlm  
1                         Negative         mlm  
2                         Negative         mlm  
3                         Negative         mlm  
4                         Negative         mlm  
...                            ...         ...  
1912  Positive; Positive; Positive      manual  
1913                      Negative      manual  
1914                      Positive      manual  
1915             Positive; Neutral      manual  
1916  Negative; Positive; Positive      manual  

[1917 rows x 6 columns]